## This is the first notebook added to the IBM Data Science Professional Certification Capstone Project ##

In [ ]:
import pandas as pd

In [ ]:
import numpy as np

In [ ]:
print("Hello Capstone Project Course!")

In [ ]:
#!pip install pyproj
#!pip install shapely

## Exploration & Data Wrangling for Final Project ##

### Dataset 1: Dining, Retail, & Other Businesses with Delivery and Takeout Service ###

In [ ]:
#Berlin Open DataSimpleSearchAPI Base URL
#http://www.berlin.de/sen/finanzen/service/zuwendungsdatenbank/index.php/index.csv?q=Test

In [1]:
import numpy as np
import pandas as pd
import requests
import urllib
import io
import json
import lxml.html as lh
import bs4 as bs
import folium
import pyproj
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values
from shapely.geometry import shape, Point
import shapely.ops as ops

In [2]:
url = 'https://www.berlin.de/sen/web/service/liefer-und-abholdienste/index.php/index/all.csv?q='
resp = requests.get(url).content
deliv_takeaw_df = pd.read_csv(io.StringIO(str(resp.decode('utf-8'))), sep=';')
deliv_takeaw_df.head()

id  unique_id               name           strasse_nr    plz  \
0  2821        963     sagrantino 136     Linienstraße 136  10115   
1  1801        617   Büroshop Koschel  Invalidenstraße 154  10115   
2  3595       1227          CAFE RIBO      Ackerstraße 157  10115   
3   526        177         Alpenstück       Gartenstraße 9  10115   
4   787        270  Risorante Bonfini    Chausseestraße 15  10115   

                                                 art  \
0  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   
1                                         Bürobedarf   
2  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   
3  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   
4  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   

                                             angebot lieferung  \
0  Italian fusion kitchen  3 -course menus by Mat...    FALSCH   
1                       Schreib- und Spielwarenladen      WAHR   
2               Maultaschen, schwäbische küche, cafe    FALSCH   
3  Süddeutsche Spezialitäten wie Maultaschen Köni...    FALSCH   
4                Italienische Küche, Pasta und Pizza    FALSCH   

  beschreibung_lieferangebot selbstabholung  ...           fon  \
0                        NaN           WAHR  ...  4.930279e+11   
1                        NaN         FALSCH  ...  4.930286e+10   
2                        NaN           WAHR  ...  4.917621e+12   
3                        NaN           WAHR  ...  4.930218e+11   
4                        NaN           WAHR  ...  4.930956e+11   

                              w3                       mail       montag  \
0  https://www.sagrantino136.com  booking@sagrantino136.com  15:00-20:00   
1      https://www.claireshop.de         info@claireshop.de          NaN   
2        https://www.caferibo.de                        NaN  09:00-16:00   
3         https://alpenstueck.de        info@alpenstueck.de  12:00-18:00   
4         https://www.bonfini.de      bestellung@bonfini.de  12:00-22:00   

      dienstag     mittwoch   donnerstag      freitag      samstag  \
0  15:00-20:00  15:00-20:00  15:00-20:00  15:00-20:00  15:00-20:00   
1          NaN          NaN          NaN          NaN          NaN   
2  09:00-16:00  09:00-16:00  09:00-16:00  09:00-16:00          NaN   
3  12:00-18:00  12:00-18:00  12:00-18:00  12:00-18:00  12:00-18:00   
4  12:00-22:00  12:00-22:00  12:00-22:00  12:00-22:00  12:00-22:00   

       sonntag  
0          NaN  
1          NaN  
2          NaN  
3  12:00-18:00  
4  12:00-22:00  

[5 rows x 21 columns]

In [3]:
deliv_takeaw_df.shape

(1248, 21)

In [4]:
deliv_takeaw_df.replace({'FALSCH':False,'WAHR':True}, inplace=True)

In [5]:
deliv_takeaw_df.head()

id  unique_id               name           strasse_nr    plz  \
0  2821        963     sagrantino 136     Linienstraße 136  10115   
1  1801        617   Büroshop Koschel  Invalidenstraße 154  10115   
2  3595       1227          CAFE RIBO      Ackerstraße 157  10115   
3   526        177         Alpenstück       Gartenstraße 9  10115   
4   787        270  Risorante Bonfini    Chausseestraße 15  10115   

                                                 art  \
0  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   
1                                         Bürobedarf   
2  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   
3  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   
4  Gastronomie (Café, Restaurant, Imbiss, Lebensm...   

                                             angebot  lieferung  \
0  Italian fusion kitchen  3 -course menus by Mat...      False   
1                       Schreib- und Spielwarenladen       True   
2               Maultaschen, schwäbische küche, cafe      False   
3  Süddeutsche Spezialitäten wie Maultaschen Köni...      False   
4                Italienische Küche, Pasta und Pizza      False   

  beschreibung_lieferangebot  selbstabholung  ...           fon  \
0                        NaN            True  ...  4.930279e+11   
1                        NaN           False  ...  4.930286e+10   
2                        NaN            True  ...  4.917621e+12   
3                        NaN            True  ...  4.930218e+11   
4                        NaN            True  ...  4.930956e+11   

                              w3                       mail       montag  \
0  https://www.sagrantino136.com  booking@sagrantino136.com  15:00-20:00   
1      https://www.claireshop.de         info@claireshop.de          NaN   
2        https://www.caferibo.de                        NaN  09:00-16:00   
3         https://alpenstueck.de        info@alpenstueck.de  12:00-18:00   
4         https://www.bonfini.de      bestellung@bonfini.de  12:00-22:00   

      dienstag     mittwoch   donnerstag      freitag      samstag  \
0  15:00-20:00  15:00-20:00  15:00-20:00  15:00-20:00  15:00-20:00   
1          NaN          NaN          NaN          NaN          NaN   
2  09:00-16:00  09:00-16:00  09:00-16:00  09:00-16:00          NaN   
3  12:00-18:00  12:00-18:00  12:00-18:00  12:00-18:00  12:00-18:00   
4  12:00-22:00  12:00-22:00  12:00-22:00  12:00-22:00  12:00-22:00   

       sonntag  
0          NaN  
1          NaN  
2          NaN  
3  12:00-18:00  
4  12:00-22:00  

[5 rows x 21 columns]

In [6]:
deliv_takeaw_df['art'].unique()

array(['Gastronomie (Café, Restaurant, Imbiss, Lebensmittelhandlung, usw.)',
       'Bürobedarf', 'Anderes (bitte bei der nächsten Frage beschreiben)',
       'Haushalt', 'Getränkemarkt', 'Baumarkt', 'Gesundheit',
       'Mode / Bekleidung', 'Möbel', 'Blumenladen', 'Buchhandlung',
       'Sportwaren (inkl. Fahrradgeschäfte)'], dtype=object)

In [7]:
deliv_takeaw_df['art'].replace({'Gastronomie (Café, Restaurant, Imbiss, Lebensmittelhandlung, usw.)':'Food service (Café, Restaurant, Diner, Grocery, etc.)',
                    'Bürobedarf':'Office Supplies','Anderes (bitte bei der nächsten Frage beschreiben)':'Other', 
                    'Haushalt':'Household','Getränkemarkt':'Beverage Store', 'Baumarkt':'Hardware Store', 'Gesundheit':'Health',
                    'Mode / Bekleidung':'Fashion / Clothing', 'Möbel':'Furniture', 'Blumenladen':'Flower Shop',
                    'Buchhandlung':'Bookstore','Sportwaren (inkl. Fahrradgeschäfte)':'Sporting Goods (incl. Bicycle Shops)'}, inplace=True)

In [8]:
deliv_takeaw_df.rename(columns={'name':'Name','plz':'Postal Code','art':'Category','lieferung':'Delivery','selbstabholung':'Takeaway'}, inplace=True)
deliv_takeaw_df.head()

id  unique_id               Name           strasse_nr  Postal Code  \
0  2821        963     sagrantino 136     Linienstraße 136        10115   
1  1801        617   Büroshop Koschel  Invalidenstraße 154        10115   
2  3595       1227          CAFE RIBO      Ackerstraße 157        10115   
3   526        177         Alpenstück       Gartenstraße 9        10115   
4   787        270  Risorante Bonfini    Chausseestraße 15        10115   

                                            Category  \
0  Food service (Café, Restaurant, Diner, Grocery...   
1                                    Office Supplies   
2  Food service (Café, Restaurant, Diner, Grocery...   
3  Food service (Café, Restaurant, Diner, Grocery...   
4  Food service (Café, Restaurant, Diner, Grocery...   

                                             angebot  Delivery  \
0  Italian fusion kitchen  3 -course menus by Mat...     False   
1                       Schreib- und Spielwarenladen      True   
2               Maultaschen, schwäbische küche, cafe     False   
3  Süddeutsche Spezialitäten wie Maultaschen Köni...     False   
4                Italienische Küche, Pasta und Pizza     False   

  beschreibung_lieferangebot  Takeaway  ...           fon  \
0                        NaN      True  ...  4.930279e+11   
1                        NaN     False  ...  4.930286e+10   
2                        NaN      True  ...  4.917621e+12   
3                        NaN      True  ...  4.930218e+11   
4                        NaN      True  ...  4.930956e+11   

                              w3                       mail       montag  \
0  https://www.sagrantino136.com  booking@sagrantino136.com  15:00-20:00   
1      https://www.claireshop.de         info@claireshop.de          NaN   
2        https://www.caferibo.de                        NaN  09:00-16:00   
3         https://alpenstueck.de        info@alpenstueck.de  12:00-18:00   
4         https://www.bonfini.de      bestellung@bonfini.de  12:00-22:00   

      dienstag     mittwoch   donnerstag      freitag      samstag  \
0  15:00-20:00  15:00-20:00  15:00-20:00  15:00-20:00  15:00-20:00   
1          NaN          NaN          NaN          NaN          NaN   
2  09:00-16:00  09:00-16:00  09:00-16:00  09:00-16:00          NaN   
3  12:00-18:00  12:00-18:00  12:00-18:00  12:00-18:00  12:00-18:00   
4  12:00-22:00  12:00-22:00  12:00-22:00  12:00-22:00  12:00-22:00   

       sonntag  
0          NaN  
1          NaN  
2          NaN  
3  12:00-18:00  
4  12:00-22:00  

[5 rows x 21 columns]

In [ ]:
#deliv_takeaw_df.to_csv(path_or_buf='~/Projects/IBMCertDS/Coursera_Capstone/data/deliv_takeaw_pre.csv')

### Dataset 2: Berlin Resident Registry 31/12/2020 ###

In [9]:
url = 'https://www.statistik-berlin-brandenburg.de/opendata/EWR_Ortsteile_2019-12-31.csv'
res_reg_df = pd.read_csv(url, encoding='latin-1', sep=';')
res_reg_df.head()

Bezirk Bez-Name  Ortsteil Ortst-Name  Geschl Staatsangeh Altersgr  \
0       1    Mitte       101      Mitte       1           A    00_05   
1       1    Mitte       101      Mitte       1           A    05_10   
2       1    Mitte       101      Mitte       1           A    10_15   
3       1    Mitte       101      Mitte       1           A    15_20   
4       1    Mitte       101      Mitte       1           A    20_25   

   Häufigkeit  
0         564  
1         435  
2         316  
3         384  
4        1329

In [10]:
res_reg_df = res_reg_df.rename(columns = {'Bez-Name': 'District', 'Ortst-Name':'Neighborhood', 'Altersgr': 'AgeGroup', 'Häufigkeit' : 'Population'} )
res_reg_df.head(10)

Bezirk District  Ortsteil Neighborhood  Geschl Staatsangeh AgeGroup  \
0       1    Mitte       101        Mitte       1           A    00_05   
1       1    Mitte       101        Mitte       1           A    05_10   
2       1    Mitte       101        Mitte       1           A    10_15   
3       1    Mitte       101        Mitte       1           A    15_20   
4       1    Mitte       101        Mitte       1           A    20_25   
5       1    Mitte       101        Mitte       1           A    25_30   
6       1    Mitte       101        Mitte       1           A    30_35   
7       1    Mitte       101        Mitte       1           A    35_40   
8       1    Mitte       101        Mitte       1           A    40_45   
9       1    Mitte       101        Mitte       1           A    45_50   

   Population  
0         564  
1         435  
2         316  
3         384  
4        1329  
5        2481  
6        3187  
7        2386  
8        1605  
9        1149

### Dataset 3: Berlin Districts ###

Get Center coordinates for Berlin and create a sampling grid to be used to query Foursquare API, requiring conversion of UTM coordinates (formatted as x,y in m) to Latitude/Longitude coordinates

In [11]:
urldistr = 'https://tsb-opendata.s3.eu-central-1.amazonaws.com/bezirksgrenzen/bezirksgrenzen.geojson'
berlin_json = requests.get(urldistr).json()

In [12]:
# create a plain world map
map_berlin_distr = folium.Map(location=[52.5200, 13.4050], zoom_start=10)


folium.GeoJson(
    berlin_json,
    name='geojson'
    ).add_to(map_berlin_distr)

map_berlin_distr

In [13]:
address = 'Berlin Germany'
geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
berlin = [location.latitude, location.longitude]

Create pyproj transformer objects for converting between UTM and Lat/Lon

In [14]:
#creating transformer objects
transform2xy = pyproj.Transformer.from_crs("+proj=latlong +ellps=WGS84" , "+proj=utm +zone=33 +ellps=WGS84")
transform2coord = pyproj.Transformer.from_crs("+proj=utm +zone=33 +ellps=WGS84" , "+proj=latlong +ellps=WGS84")

#applying transformer objects of the transform method on Berlin coordinates
x, y = transform2xy.transform(berlin[1], berlin[0])
lon, lat = transform2coord.transform(x,y)
print('Berlin center coordinate, Lon= {}; Lat= {}'.format(berlin[1], berlin[0]))
print('Berlin center transform to UTM, X= {}; Y= {}'.format(x,y))
print('Berlin center reverse transform, Lon= {}; Lat= {}'.format(lon, lat))

Berlin center coordinate, Lon= 13.3888599; Lat= 52.5170365
Berlin center transform to UTM, X= 390676.87103088724; Y= 5819766.874314442
Berlin center reverse transform, Lon= 13.3888599; Lat= 52.51703649999999


Alternatively, a single Pyproj projector object can be used, inverted from xy to latlong using argument 'inverse=True'

In [15]:
proj2xy = pyproj.Proj(proj='utm',zone=33,ellps='WGS84', always_xy=False)

x, y = proj2xy(berlin[1], berlin[0])
lon, lat = proj2xy(x,y, inverse=True)
print('Berlin center coordinate, Lon= {}; Lat= {}'.format(berlin[1], berlin[0]))
print('Berlin center transform to UTM, X= {}; Y= {}'.format(x,y))
print('Berlin center reverse transform, Lon= {}; Lat= {}'.format(lon, lat))

Berlin center coordinate, Lon= 13.3888599; Lat= 52.5170365
Berlin center transform to UTM, X= 390676.87103088724; Y= 5819766.874314442
Berlin center reverse transform, Lon= 13.3888599; Lat= 52.51703649999999


**NOTE ON TRANSFORMER OBJECTS:** The transformer objects above have been updated to meet current pyproj conventionn (pyproj2 format still in use for pyproj3) based on TobGerken's Pulse of Berlin project, which used the now deprecated procedure from pyproj1.  The deprecated pyproj1 procedure, involving creation of definitions combining pyproj Proj and pyproj transform to convert between two CRSs, is shown below:

In [ ]:
# def lonlat2xy(lat,lon):
#    proj_coord = pyproj.Proj(proj='latlong',datum='WGS84')
#    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
#    xy = pyproj.transform(proj_coord, proj_xy, lon,lat)
#    return xy[0], xy[1]
    
# def xy2lonlat(x,y):
#    proj_coord = pyproj.Proj(proj='latlong',datum='WGS84')
#    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
#    coord = pyproj.transform(proj_xy, proj_coord, x, y)
#    return coord[0], coord[1]

# #apply transformer definitions on Berlin coordinates
# x, y = lonlat2xy(berlin[0], berlin[1])
# lon, lat = xy2lonlat(x,y)
# print('Berlin center coordinate, Lon= {}; Lat= {}'.format(berlin[1], berlin[0]))
# print('Berlin center transform to UTM, X= {}; Y= {}'.format(x,y))
# print('Berlin center reverse transform, Lon= {}; Lat= {}'.format(lon, lat))

### Loop through selected polygons to create dataframe of representative points, and polygon area ###

In [16]:
urlzip = 'https://tsb-opendata.s3.eu-central-1.amazonaws.com/plz/plz.geojson'
berlinzip_json = requests.get(urlzip).json()

In [17]:
map_berlin_zip = folium.Map(location=[52.5200, 13.4050], zoom_start=10)


folium.GeoJson(
    berlinzip_json,
    name='geojson'
    ).add_to(map_berlin_zip)

map_berlin_zip

In [18]:
area = []
lats = []
lons = []
name = []

for feature in berlinzip_json['features']:
        name.append(feature['properties']['plz'])
        polygon = shape(feature['geometry'])
        p=polygon.representative_point()
        lons.append(p.x)
        lats.append(p.y)
        
        geom_aea = ops.transform(
            pyproj.Proj(
            proj='aea',
            lat_1=polygon.bounds[1],
            lat_2=polygon.bounds[3]),
        polygon)
        a = geom_aea.area/1000**2
        area.append(a)
        #print(feature['properties']['spatial_name']) 
        #if polygon.contains(point):
            #print(feature['properties']['spatial_name'])
        #    zips[ct] = feature['properties']['spatial_name']       

        

ZIPS = pd.DataFrame(data={'ZIP':name, 'Latitude':lats, 'Longitude':lons, 'Area':area})
ZIPS = ZIPS.iloc[0:191,:]
ZIPS.sort_values(['ZIP'], ascending=True, axis=0, inplace=True)
ZIPS

ZIP   Latitude  Longitude       Area
0    10115  52.531967  13.383747   2.307098
1    10117  52.517480  13.387818   3.441065
2    10119  52.530124  13.405504   0.975444
3    10178  52.520294  13.404317   1.858672
4    10179  52.513815  13.415303   2.199530
..     ...        ...        ...        ...
175  14193  52.481345  13.238469  20.706761
185  14193  52.481345  13.238469  20.706761
186  14195  52.458581  13.284630   8.104204
187  14197  52.473179  13.310292   1.585814
188  14199  52.477962  13.292422   2.412821

[191 rows x 4 columns]

For some reason ZIP-14193 is duplicated from this process, although it is not duplicate in the geoJSON file, so we must drop the duplicate and reset the index as done below

In [19]:
ZIPS.drop_duplicates(inplace=True)
ZIPS.reset_index(drop=True, inplace=True)
ZIPS

ZIP   Latitude  Longitude       Area
0    10115  52.531967  13.383747   2.307098
1    10117  52.517480  13.387818   3.441065
2    10119  52.530124  13.405504   0.975444
3    10178  52.520294  13.404317   1.858672
4    10179  52.513815  13.415303   2.199530
..     ...        ...        ...        ...
185  14169  52.449996  13.258822   5.102470
186  14193  52.481345  13.238469  20.706761
187  14195  52.458581  13.284630   8.104204
188  14197  52.473179  13.310292   1.585814
189  14199  52.477962  13.292422   2.412821

[190 rows x 4 columns]

In [ ]:
# ZIPS.to_csv(path_or_buf='~/Projects/IBMCertDS/Coursera_Capstone/out_of_git_data/ZIPS.csv')

In [60]:
parseurl = "https://www.berlinstadtservice.de/xinh/Postleitzahlen_Berlin_Zahlen.html"
resp = requests.get(parseurl)
soup = bs.BeautifulSoup(resp.content,'lxml')
table = soup.find_all('table')[0]
df = pd.read_html(str(table))
webdata = pd.read_json(df[0].to_json(orient='records'))
webdata.rename(columns={'Berlin Postleitzahl 101..':'values'}, inplace=True)

In [61]:
webdata = webdata[~webdata['values'].str.contains('Postleitzahl')]
webdata.reset_index(drop=True, inplace=True)
webdata[['PLZ', 'Ortsteil']] = webdata['values'].str.split(' ', 1, expand=True)
webdata['Ortsteil'] = webdata['Ortsteil'].str.replace('B- ','')
webdata = webdata[['PLZ','Ortsteil']]
webdata.head(20)

PLZ         Ortsteil
0   10115            Mitte
1   10117            Mitte
2   10119            Mitte
3   10178            Mitte
4   10179            Mitte
5   10243   Friedrichshain
6   10243   Friedrichshain
7   10247   Friedrichshain
8   10247  Prenzlauer Berg
9   10249   Friedrichshain
10  10249  Prenzlauer Berg
11  10315  Friedrichsfelde
12  10317  Friedrichsfelde
13  10317      Lichtenberg
14  10317      Rummelsburg
15  10318  Friedrichsfelde
16  10318       Karlshorst
17  10319  Friedrichsfelde
18  10365      Lichtenberg
19  10367      Lichtenberg

In [ ]:
# webdata.to_csv(path_or_buf='~/Projects/IBMCertDS/Coursera_Capstone/out_of_git_data/plz_neightborhood_unproc.csv')

In [ ]:
# webdata = webdata.append(pd.DataFrame([['13507','Tegel']], columns
# =webdata.columns))

This list found on the web had two errors where one zip code is listed twice as another is left out.  We must replace duplicate 10243 and 13505 with 10245 and 13507, respectively.

In [66]:
webdata.loc[6,'PLZ'] = 10245
webdata.loc[257,'PLZ'] = 13507
#mixed data types in PLZ column, must be converted to int to sort
webdata['PLZ'] = webdata['PLZ'].astype(int)
webdata.sort_values(['PLZ'], ascending=True, axis=0, inplace=True)

Group and aggregate Neighborhoods according to shared postal codes, setting up for merging datasets

In [67]:
webdata = webdata.groupby(['PLZ'], as_index=False).agg(','.join)
webdata.reset_index(drop=True, inplace=True)
webdata

PLZ                                   Ortsteil
0    10115                                      Mitte
1    10117                                      Mitte
2    10119                                      Mitte
3    10178                                      Mitte
4    10179                                      Mitte
..     ...                                        ...
185  14169                          Zehlendorf,Dahlem
186  14193  Dahlem,Grunewald,Nikolassee,Schmargendorf
187  14195           Wilmersdorf,Dahlem,Schmargendorf
188  14197                                Wilmersdorf
189  14199        Schmargendorf,Grunewald,Wilmersdorf

[190 rows x 2 columns]

In [70]:

webdata.head(30)

PLZ                                 Ortsteil
0   10115                                    Mitte
1   10117                                    Mitte
2   10119                                    Mitte
3   10178                                    Mitte
4   10179                                    Mitte
5   10243                           Friedrichshain
6   10245                           Friedrichshain
7   10247           Friedrichshain,Prenzlauer Berg
8   10249           Prenzlauer Berg,Friedrichshain
9   10315                          Friedrichsfelde
10  10317  Friedrichsfelde,Lichtenberg,Rummelsburg
11  10318               Friedrichsfelde,Karlshorst
12  10319                          Friedrichsfelde
13  10365                              Lichtenberg
14  10367                              Lichtenberg
15  10369                              Lichtenberg
16  10405                          Prenzlauer Berg
17  10407                          Prenzlauer Berg
18  10409                          Prenzlauer Berg
19  10435                    Mitte,Prenzlauer Berg
20  10437                          Prenzlauer Berg
21  10439                   Pankow,Prenzlauer Berg
22  10551                               Tiergarten
23  10553                               Tiergarten
24  10555                               Tiergarten
25  10557                               Tiergarten
26  10559                               Tiergarten
27  10585                           Charlottenburg
28  10587                           Charlottenburg
29  10589                           Charlottenburg

In [ ]:
webdata.head(30)

In [ ]:
# webdata.to_csv(path_or_buf='~/Projects/IBMCertDS/Coursera_Capstone/out_of_git_data/plz_neightborhood.csv')

In [ ]:
parseurl1 = "https://de.wikipedia.org/wiki/Verwaltungsgliederung_Berlins"
resp1 = requests.get(parseurl1)
soup1 = bs.BeautifulSoup(resp1.content,'lxml')
table1 = soup1.find_all('table')[1]
df1 = pd.read_html(str(table1))
webdata1 = pd.read_json(df1[0].to_json(orient='records'))
webdata1 = webdata1[['Ortsteil','Bezirk']]
webdata1.head()

In [ ]:
# area = []
# lats = []
# lons = []
# name = []

# for feature in js['features']:
#         name.append(feature['properties']['spatial_name'])
#         polygon = shape(feature['geometry'])
#         p=polygon.representative_point()
#         lons.append(p.x)
#         lats.append(p.y)
        
#         geom_aea = ops.transform(
#             partial(
#             pyproj.transform,
#             pyproj.Proj(init='EPSG:4326'),
#             pyproj.Proj(
#             proj='aea',
#             lat_1=polygon.bounds[1],
#             lat_2=polygon.bounds[3])),
#         polygon)
#         a = geom_aea.area/1000**2
#         area.append(a)
#         #print(feature['properties']['spatial_name']) 
#         #if polygon.contains(point):
#             #print(feature['properties']['spatial_name'])
#         #    zips[ct] = feature['properties']['spatial_name']       

        

# ZIPS = pd.DataFrame(data={'ZIP':name, 'Latitude':lats, 'Longitude':lons, 'Area':area})
# berlin_merged =ZIPS.merge(b_venues,how='left', left_on='ZIP', right_on='Venue ZIP')
# berlin_merged.head()

Choose x,y grid of 2km spacing

In [ ]:
x_center, y_center = proj2xy(berlin[0], berlin[1])
XX = np.arange(-20,26,1)*1000 + x_center
YY = np.arange(20,-21,-1)*1000 + y_center

In [ ]:
Lats =[]
Lons = []

for y in YY:
    for x in XX:
        lon, lat =proj2xy(x,y, inverse=True)
        Lats.append(lat)
        Lons.append(lon)

In [ ]:
df_points = pd.DataFrame(columns = ['Latitude','Longitude', 'District'])
    
map_berlin = folium.Map(location=[52.5200, 13.4050], zoom_start=10)
folium.GeoJson(
    berlin_json,
    name='geojson'
).add_to(map_berlin)



for lon, lat in zip(Lons ,Lats):
    point = Point(lon, lat)
    for feature in berlin_json['features']:
        polygon = shape(feature['geometry'])
        #print(feature['properties']['Gemeinde_name'])
        if polygon.contains(point):
            #print(feature['properties']['Gemeinde_name'])
            df_points = df_points.append({'Latitude': lat, 'Longitude': lon, 'District':feature['properties']['Gemeinde_name'] 
                                         }, ignore_index=True)

            folium.features.CircleMarker(
                [lat, lon],
                radius=2, # define how big you want the circle markers to be
                color='yellow',
                fill=True,
                fill_color='yellow',
                popup = 'Lat={:5.2f}; Lon={:5.2f}'.format(lat, lon),
                fill_opacity=0.9
            ).add_to(map_berlin)
            
map_berlin

In [ ]:
berlin_json

In [ ]:
df_points